In [4]:
import plotly.express as px
import pandas as pd
import json
import numpy as np


path = "tl_2018_nm_county.geojson"
with open(path) as f:
    counties = json.load(f)


df = pd.DataFrame({
    'county': [county['properties']['NAME'] for county in counties['features']],
    'yield': np.zeros(shape=len(counties['features']))  
})

yield_df = pd.read_csv('../../data/pecan/yield_05_23_24.csv')
yield_df['County'] = yield_df['County'].str.replace('County', '').str.strip()
yield_df['Value'] = yield_df['Value'].str.replace(',', '').astype(int)
county_yields = yield_df.groupby('County')['Value'].sum().reset_index()
df = df.merge(county_yields, how='left', left_on='county', right_on='County')
df['Value'] = df['Value'].fillna(0)
df['yield'] += df['Value']
df = df.drop(columns=['County', 'Value'])



class ChoroplethMap:
    def __init__(self, df, counties, title, locations='county', color='yield'):
        self.df = df
        self.counties = counties
        self.title = title
        self.color = color
        self.locations = locations
        self.fig = None
        self.color_scale = [
            [0, '#d8dee9'],    # Darkest grey
            [0.1, '#3B4252'],  # Dark grey
            [0.2, '#434C5E'],  # Medium-dark grey
            [0.3, '#4C566A'],  # Medium grey
            [0.4, '#516173'],  # Grey with slight blue tint
            [0.5, '#5B6B7C'],  # Blueish grey
            [0.6, '#5E81AC'],  # Dark Nord blue
            [0.7, '#6D90BA'],  # Medium-dark Nord blue
            [0.8, '#7B9FC8'],  # Medium Nord blue
            [0.9, '#88AED6'],  # Medium-light Nord blue
            [1, '#95BDE4']     # Nord blue
        ]

    def plot(self):
        self.fig = px.choropleth(
            self.df,
            geojson=self.counties,
            locations=self.locations,
            color=self.color,
            featureidkey="properties.NAME",
            projection='mercator',
            color_continuous_scale=self.color_scale,
            labels={self.color: 'Yield'},

        )

        self.fig.update_geos(
            fitbounds="locations",
            visible=False,
            bgcolor='#eceff4',

        )


        self.fig.update_layout(
            # title_text=self.title,
            title=dict(text=self.title, font=dict(size=30)),
            paper_bgcolor='#eceff4',
            plot_bgcolor='#eceff4',
            title_x=0.5,
            title_y=0.95,
            width=800,  # Increase the overall width
            height=800,  # Increase the overall height
            margin=dict(l=20, r=20, t=40, b=20),  # Reduce margins
            coloraxis_colorbar=dict(
                title='Yield',
                thicknessmode="pixels", thickness=40,
                lenmode="fraction", len=0.75,
                yanchor="top", y=.95,
                xanchor="left", x=.95
            )

        )

        self.fig.show()

    def save(self, file_path):
        if self.fig:
            self.fig.write_html(file_path)


title = "County Yields"
choropleth_map = ChoroplethMap(df, counties, title)

choropleth_map.plot()
choropleth_map.save('geojson.html')

